## Separate img files and text files

In [9]:
import os
import shutil

FRUIT_PATH = 'YOUR_FRUIT_PATH'
DEST_PATH = 'YOUR_DEST_PATH'
path = os.listdir(FRUIT_PATH)

for file_name in path:
    if file_name.endswith('.png'):
        shutil.move(os.path.join(FRUIT_PATH,file_name), os.path.join(DEST_PATH,file_name))

## Convert YOLO to xml files

In [11]:
from lxml import etree
from PIL import Image
import csv
import os

# (NOTICE #1)
# If you're OS is Mac, there's a case when '.DS_Store' file is  automatically created.
# In that case, you have to remove '.DS_Store' file through the terminal.
# Ref : http://leechoong.com/posts/2018/ds_store/
# (NOTICE #2)
# Change this path variable
IMG_PATH = "YOUR_IMG_PATH"
fw = os.listdir(IMG_PATH)
# path of save xml file
save_path = 'Orange_xml' # keep it blank

# txt_folder is txt file root that using darknet rectbox
txt_folder = 'YOUR_TXT_PATH'

# (NOTICE #3)
# Change this labels
labels = ['YOUR_LABELS']
global label
label = ''

def csvread(fn):
    with open(fn, 'r') as csvfile:
        list_arr = []
        reader = csv.reader(csvfile, delimiter=' ')

        for row in reader:
            list_arr.append(row)
    return list_arr


def convert_label(txt_file):
    global label
    for i in range(len(labels)):
        if txt_file[0] == str(i):
            label = labels[i]
            return label

    return label

# core code = convert the yolo txt file to the x_min,x_max...


def extract_coor(txt_file, img_width, img_height):
    x_rect_mid = float(txt_file[1])
    y_rect_mid = float(txt_file[2])
    width_rect = float(txt_file[3])
    height_rect = float(txt_file[4])

    x_min_rect = ((2 * x_rect_mid * img_width) - (width_rect * img_width)) / 2
    x_max_rect = ((2 * x_rect_mid * img_width) + (width_rect * img_width)) / 2
    y_min_rect = ((2 * y_rect_mid * img_height) -
                  (height_rect * img_height)) / 2
    y_max_rect = ((2 * y_rect_mid * img_height) +
                  (height_rect * img_height)) / 2

    return x_min_rect, x_max_rect, y_min_rect, y_max_rect


for line in fw:
    root = etree.Element("annotation")

    # try debug to check your path
    img_style = IMG_PATH.split('/')[-1]
    img_name = line
    image_info = IMG_PATH + "/" + line
    img_txt_root = txt_folder + "/" + line[:-4]
    # print(img_txt_root)
    txt = ".txt"

    txt_path = img_txt_root + txt
    # print(txt_path)
    txt_file = csvread(txt_path)
    ######################################

    # read the image  information
    img_size = Image.open(image_info).size

    img_width = img_size[0]
    img_height = img_size[1]
    # img_depth = Image.open(image_info).layers
    ######################################

    folder = etree.Element("folder")
    folder.text = "%s" % (img_style)

    filename = etree.Element("filename")
    filename.text = "%s" % (img_name)

    path = etree.Element("path")
    path.text = "%s" % (IMG_PATH)

    source = etree.Element("source")
    ##################source - element##################
    source_database = etree.SubElement(source, "database")
    source_database.text = "Unknown"
    ####################################################

    size = etree.Element("size")
    ####################size - element##################
    image_width = etree.SubElement(size, "width")
    image_width.text = "%d" % (img_width)

    image_height = etree.SubElement(size, "height")
    image_height.text = "%d" % (img_height)

    image_depth = etree.SubElement(size, "depth")
#     image_depth.text = "%d" % (img_depth)
    ####################################################

    segmented = etree.Element("segmented")
    segmented.text = "0"

    root.append(folder)
    root.append(filename)
    root.append(path)
    root.append(source)
    root.append(size)
    root.append(segmented)

    for ii in range(len(txt_file)):
        label = 'YOUR_LABEL'
        x_min_rect, x_max_rect, y_min_rect, y_max_rect = extract_coor(
            txt_file[ii], img_width, img_height)

        object = etree.Element("object")
        ####################object - element##################
        name = etree.SubElement(object, "name")
        name.text = "%s" % (label)

        pose = etree.SubElement(object, "pose")
        pose.text = "Unspecified"

        truncated = etree.SubElement(object, "truncated")
        truncated.text = "0"

        difficult = etree.SubElement(object, "difficult")
        difficult.text = "0"

        bndbox = etree.SubElement(object, "bndbox")
        #####sub_sub########
        xmin = etree.SubElement(bndbox, "xmin")
        xmin.text = "%d" % (x_min_rect)
        ymin = etree.SubElement(bndbox, "ymin")
        ymin.text = "%d" % (y_min_rect)
        xmax = etree.SubElement(bndbox, "xmax")
        xmax.text = "%d" % (x_max_rect)
        ymax = etree.SubElement(bndbox, "ymax")
        ymax.text = "%d" % (y_max_rect)
        #####sub_sub########

        root.append(object)
        ####################################################

    file_output = etree.tostring(root, pretty_print=True, encoding='UTF-8')
    print(file_output.decode('utf-8'))
    ff = open('%s.xml' % (img_name[:-4]), 'w', encoding="utf-8")
    ff.write(file_output.decode('utf-8'))

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach001.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>480</width>
    <height>322</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>265</xmin>
      <ymin>42</ymin>
      <xmax>385</xmax>
      <ymax>149</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>207</xmin>
      <ymin>0</ymin>
      <xmax>313</xmax>
      <ymax>47</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>358</xmin>
      <ymin>18</ymi

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach001076.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>132</xmin>
      <ymin>156</ymin>
      <xmax>210</xmax>
      <ymax>245</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>99</xmin>
      <ymin>27</ymin>
      <xmax>172</xmax>
      <ymax>110</ymax>
    </bndbox>
  </object>
</annotation>

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach001077.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach001156.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>97</xmin>
      <ymin>37</ymin>
      <xmax>176</xmax>
      <ymax>116</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>81</xmin>
      <ymin>112</ymin>
      <xmax>158</xmax>
      <ymax>191</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>197</xmin>
      <ymin>122

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach001186.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>169</xmin>
      <ymin>26</ymin>
      <xmax>239</xmax>
      <ymax>108</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>65</xmin>
      <ymin>19</ymin>
      <xmax>139</xmax>
      <ymax>100</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>154</xmin>
      <ymin>142

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach001252.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>22</xmin>
      <ymin>45</ymin>
      <xmax>98</xmax>
      <ymax>130</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>0</xmin>
      <ymin>127</ymin>
      <xmax>103</xmax>
      <ymax>226</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>87</xmin>
      <ymin>0</ymi

...

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach0093.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>78</xmin>
      <ymin>7</ymin>
      <xmax>161</xmax>
      <ymax>108</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>0</xmin>
      <ymin>131</ymin>
      <xmax>75</xmax>
      <ymax>242</ymax>
    </bndbox>
  </object>
</annotation>

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach00930.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach00943.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>129</xmin>
      <ymin>94</ymin>
      <xmax>217</xmax>
      <ymax>197</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>189</xmin>
      <ymin>63</ymin>
      <xmax>270</xmax>
      <ymax>144</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>61</xmin>
      <ymin>58</

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach00964.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>198</xmin>
      <ymin>0</ymin>
      <xmax>279</xmax>
      <ymax>71</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>140</xmin>
      <ymin>81</ymin>
      <xmax>237</xmax>
      <ymax>173</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>58</xmin>
      <ymin>54</ym

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach00980.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>142</xmin>
      <ymin>81</ymin>
      <xmax>238</xmax>
      <ymax>173</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>99</xmin>
      <ymin>0</ymin>
      <xmax>173</xmax>
      <ymax>72</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>58</xmin>
      <ymin>54</ymi

<annotation>
  <folder>D:\Object_detection_data\obj\Peach_img</folder>
  <filename>Peach00991.png</filename>
  <path>D:\Object_detection_data\obj\Peach_img</path>
  <source>
    <database>Unknown</database>
  </source>
  <size>
    <width>320</width>
    <height>258</height>
    <depth/>
  </size>
  <segmented>0</segmented>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>20</xmin>
      <ymin>123</ymin>
      <xmax>121</xmax>
      <ymax>225</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>60</xmin>
      <ymin>53</ymin>
      <xmax>138</xmax>
      <ymax>132</ymax>
    </bndbox>
  </object>
  <object>
    <name>Peach</name>
    <pose>Unspecified</pose>
    <truncated>0</truncated>
    <difficult>0</difficult>
    <bndbox>
      <xmin>135</xmin>
      <ymin>133<